## Tutorial on how to 'delay' the start of particle advection

In many applications, it is needed to 'delay' the start of particle advection. For example because particles need to be released at different times throughout an experiment. Or because particles need to be released at a constant rate from the same set of locations.

This tutorial will show how this can be done. We start with importing the relevant modules.

In [1]:
%matplotlib inline
from parcels import FieldSet, ParticleSet, JITParticle, plotTrajectoriesFile
from parcels import AdvectionRK4
import numpy as np
import xarray as xr
from datetime import timedelta as delta

First import a `FieldSet` (from the Peninsula example, in this case)

In [2]:
fieldset = FieldSet.from_parcels('Peninsula_data/peninsula', allow_time_extrapolation = True)

Now, there are two ways to delay the start of particles. Either by defining the whole `ParticleSet` at initialisation and giving each particle its own `time`. Or by using the `repeatdt` argument. We will show both options here

### Assigning each particle its own `time` ###

The simplest way to delaye the start of a particle is to use the `time` argument for each particle

In [3]:
npart = 10  # number of particles to be released
lon = 3e3 * np.ones(npart)
lat = np.linspace(3e3 , 45e3, npart, dtype=np.float32)
time = np.arange(0, npart) * delta(hours=1).total_seconds()  # release every particle one hour later

pset = ParticleSet(fieldset=fieldset, pclass=JITParticle, lon=lon, lat=lat, time=time)

Then we can execute the `pset` as usual

In [4]:
output_file = pset.ParticleFile(name="DelayParticle_time.nc", outputdt=delta(hours=1))
pset.execute(AdvectionRK4, runtime=delta(hours=24), dt=delta(minutes=5),
             output_file=output_file)
output_file.export()  # export the trajectory data to a netcdf file

INFO: Compiled ArrayJITParticleAdvectionRK4 ==> /var/folders/r2/8593q8z93kd7t4j9kbb_f7p00000gr/T/parcels-504/lib15ab640308c954e580b6f93be742baae_0.so


And then finally, we can show a movie of the particles. Note that the southern-most particles start to move first.

In [5]:
plotTrajectoriesFile('DelayParticle_time.nc', mode='movie2d_notebook')

### Using the `repeatdt` argument ###

The second method to delay the start of particle releases is to use the `repeatdt` argument when constructing a `ParticleSet`. This is especially useful if you want to repeatedly release particles from the same set of locations.

In [6]:
npart = 10  # number of particles to be released
lon = 3e3 * np.ones(npart)
lat = np.linspace(3e3 , 45e3, npart, dtype=np.float32)
repeatdt = delta(hours=3)  # release from the same set of locations every 3 hours

pset = ParticleSet(fieldset=fieldset, pclass=JITParticle, lon=lon, lat=lat, repeatdt=repeatdt)

Now we again define an output file and execute the `pset` as usual.

In [7]:
output_file = pset.ParticleFile(name="DelayParticle_releasedt", outputdt=delta(hours=1))
pset.execute(AdvectionRK4, runtime=delta(hours=24), dt=delta(minutes=5),
             output_file=output_file)

INFO: Compiled ArrayJITParticleAdvectionRK4 ==> /var/folders/r2/8593q8z93kd7t4j9kbb_f7p00000gr/T/parcels-504/libcbcec39cf73cfa7671e8798abaac733b_0.so


And we get an animation where a new particle is released every 3 hours from each start location

In [8]:
output_file.export()  # export the trajectory data to a netcdf file
plotTrajectoriesFile('DelayParticle_releasedt.nc', mode='movie2d_notebook')

Note that, if you want to if you want to at some point stop the repeatdt, the easiest implementation is to use two calls to `pset.execute()`. For example, if in the above example you only want four releases of the pset, you could do the following

In [9]:
pset = ParticleSet(fieldset=fieldset, pclass=JITParticle, lon=lon, lat=lat, repeatdt=repeatdt)
output_file = pset.ParticleFile(name="DelayParticle_releasedt_9hrs", outputdt=delta(hours=1))

# first run for 3 * 3 hrs
pset.execute(AdvectionRK4, runtime=delta(hours=9), dt=delta(minutes=5),
             output_file=output_file)

# now stop the repeated release
pset.repeatdt = None

# now continue running for the remaining 15 hours
pset.execute(AdvectionRK4, runtime=delta(hours=15), dt=delta(minutes=5),
             output_file=output_file)

output_file.export()  # export the trajectory data to a netcdf file
plotTrajectoriesFile('DelayParticle_releasedt_9hrs.nc', mode='movie2d_notebook')

INFO: Compiled ArrayJITParticleAdvectionRK4 ==> /var/folders/r2/8593q8z93kd7t4j9kbb_f7p00000gr/T/parcels-504/libd1c17d6554e6d39a5c989beb50bcc2d3_0.so


### Synced `time` in the output file

Note that, because the `outputdt` variable controls the JIT-loop, all particles are written _at the same time_, even when they start at a non-multiple of `outputdt`. 

For example, if your particles start at `time=[0, 1, 2]` and `outputdt=2`, then the times written (for `dt=1` and `endtime=4`) will be 

In [10]:
outtime_expected = np.array([[0, 2, 4], [2, 4, np.datetime64("NaT")], [2, 4, np.datetime64("NaT")]], dtype="timedelta64[s]")
print(outtime_expected)

[[    0     2     4]
 [    2     4 'NaT']
 [    2     4 'NaT']]


In [11]:
outfilepath = "DelayParticle_nonmatchingtime.nc"

pset = ParticleSet(fieldset=fieldset, pclass=JITParticle,
                   lat=[3e3]*3, lon=[3e3]*3, time=[0, 1, 2])
pset.execute(AdvectionRK4, endtime=4, dt=1, output_file=pset.ParticleFile(name=outfilepath, outputdt=2))

INFO: Compiled ArrayJITParticleAdvectionRK4 ==> /var/folders/r2/8593q8z93kd7t4j9kbb_f7p00000gr/T/parcels-504/lib73f1058452aa339434e56df780d0ba46_0.so


And indeed, the `time` values in the NetCDF output file are as expected

In [12]:
outtime_infile = xr.open_dataset(outfilepath).time.values[:]
print(outtime_infile.astype('timedelta64[s]'))

assert (outtime_expected[np.isfinite(outtime_expected)] == outtime_infile[np.isfinite(outtime_infile)]).all()

[[    0     2     4]
 [    2     4 'NaT']
 [    2     4 'NaT']]


Now, for some applications, this behavior may be undesirable; for example when particles need to be analyzed at a same age (instead of at a same time). In that case, we recommend either changing `outputdt` so that it is a common divisor of all start times; or doing multiple Parcels runs with subsets of the original `ParticleSet` (e.g., in the example above, one run with the Particles that start at `time=[0, 2]` and one with the Particle at `time=[1]`). In that case, you will get two files:

In [13]:
for times in [[0,2], [1]]:
    pset = ParticleSet(fieldset=fieldset, pclass=JITParticle,
                       lat=[3e3]*len(times), lon=[3e3]*len(times), time=times)
    pset.execute(AdvectionRK4, endtime=4, dt=1, output_file=pset.ParticleFile(name=outfilepath, outputdt=2))
    print(xr.open_dataset(outfilepath).time.values[:].astype('timedelta64[s]'))

INFO: Compiled ArrayJITParticleAdvectionRK4 ==> /var/folders/r2/8593q8z93kd7t4j9kbb_f7p00000gr/T/parcels-504/lib4a9283c7ab81279666f072b74de9d644_0.so


[[    0     2     4]
 [    2     4 'NaT']]


INFO: Compiled ArrayJITParticleAdvectionRK4 ==> /var/folders/r2/8593q8z93kd7t4j9kbb_f7p00000gr/T/parcels-504/libef5ef37165aa5febcc2e916a89504269_0.so


[[1 3 4]]
